# Introduction

**Executive summary:** use `WalkForwardRunner` to run your walk-forward training, use `WalkForwardResults` to restore the agent and visualize the results.

In [10]:
import ray
from ray import rllib, tune
import pandas as pd
from datetime import datetime
import trading_gym
from trading_gym.registry.gaia.v7.env import GAIAPredictorsContinuousV7
from trading_gym.registry.gaia.v8.env import GAIAPredictorsContinuousV8
from trading_gym.ray.walkforward import WalkForwardRunner, WalkForwardResults
import os
%matplotlib inline
print(trading_gym.__package__, trading_gym.__version__)
print(ray.__package__, ray.__version__)

trading-gym 0.8.1
ray 0.7.2


In [11]:
ray.init(ignore_reinit_error=True)

2019-07-23 08:39:06,127	ERROR worker.py:1343 -- Calling ray.init() again after it has already been called.


# WalkForwardRunner
In pure `ray`, you are used to do something along the lines of what follows:

    config = ray.rllib.agents.ppo.DEFAULT_CONFIG.copy()
    config['env'] = GAIAPredictorsContinuousV8
    config['env_config'] = {'cost_of_commissions': 0.00005, 'cost_of_spread': 0.0001}
    tune.run(
        PPOTrainer,
        config=config,
        stop={'timesteps_total': 25000},
        checkpoint_freq=1,
        verbose=1,
    )
    
In this section we see how to reproduce the same logic using `WalkForwardRunner`. The benefit of using `WalkForwardRunner` as opposed to pure `ray` is that only the former allows to use `WalkForwardResults` to restore and visualize agents on different folds.

## Create the walk-forward partitions
It's responsibility of the user to create the training/test (and maybe validation) partitions to turn the walk forward training. Note that 2-fold split is a particular case of walk-forward training, so you are still able to run a simple 2-fold split.

In [12]:
partitions = list()
for year in range(2007, 2009):
    partition = {
        'training-set': [datetime.min, datetime(year, 12, 31)],
        'test-set': [datetime(year + 1, 1, 1), datetime(year + 1, 12, 31)],
    }
    partitions.append(partition)
partitions

[{'training-set': [datetime.datetime(1, 1, 1, 0, 0),
   datetime.datetime(2007, 12, 31, 0, 0)],
  'test-set': [datetime.datetime(2008, 1, 1, 0, 0),
   datetime.datetime(2008, 12, 31, 0, 0)]},
 {'training-set': [datetime.datetime(1, 1, 1, 0, 0),
   datetime.datetime(2008, 12, 31, 0, 0)],
  'test-set': [datetime.datetime(2009, 1, 1, 0, 0),
   datetime.datetime(2009, 12, 31, 0, 0)]}]

## Create the config dict


In [13]:
config = ray.rllib.agents.ppo.DEFAULT_CONFIG.copy()
config['env'] = GAIAPredictorsContinuousV8
config['env_config'] = {
    'cost_of_commissions': tune.grid_search([0.00005]), # 0.00005 and 0.0001 defaukt
    'cost_of_spread': 0.0001, # 0.0001
}

config['vf_clip_param'] = 0
config['vf_loss_coeff'] = 0
config['lambda'] = 0
config['use_gae'] = False
config['vf_share_layers'] = False 
config['use_lstm']: False
config['batch_mode'] = 'complete_episodes'
config['train_batch_size'] = tune.grid_search([4000])
config['sgd_minibatch_size'] = 128
config['num_sgd_iter'] = tune.grid_search([8])
config['entropy_coeff'] = tune.grid_search([1e-5])
config['kl_coeff'] = tune.grid_search([0.2])
config['kl_target'] = tune.grid_search([0.01])
config['clip_param'] = tune.grid_search([0.1,0.2,0.3,0.4,0.5,0.6])

config['lr'] = tune.grid_search([1e-5])
config['gamma'] = tune.grid_search([1e-5])

## Run your walk-forward experiment

In [14]:
walk_forward = WalkForwardRunner(
    env_partitions=partitions,
    trainable=ray.rllib.agents.ppo.PPOTrainer,
    config=config,
    stop={'timesteps_total': 300000},
    checkpoint_freq=1,
)

Note that WalkForwardRunner has constructed the implied ray Experiment(s) from your walk forward settings.

In [7]:
# trials = tune.run_experiments(walk_forward.experiments, verbose=0)
trials = walk_forward.run(verbose=1)

2019-07-18 16:43:26,993	WARNING experiment.py:218 -- All experiments will be using the same SearchAlgorithm.
2019-07-18 16:43:26,999	INFO tune.py:61 -- Tip: to resume incomplete experiments, pass resume='prompt' or resume=True to run()
2019-07-18 16:43:27,001	INFO tune.py:233 -- Starting a new experiment.
2019-07-18 16:43:27,156	WARNING signature.py:108 -- The function with_updates has a **kwargs argument, which is currently not supported.


== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/8 CPUs, 0/0 GPUs
Memory usage on this node: 41.4/67.5 GB



2019-07-18 16:43:27,302	WARNING util.py:64 -- The `start_trial` operation took 0.15354108810424805 seconds to complete, which may be a performance bottleneck.
2019-07-18 16:43:27,365	WARNING signature.py:108 -- The function with_updates has a **kwargs argument, which is currently not supported.
2019-07-18 16:43:27,496	WARNING util.py:64 -- The `start_trial` operation took 0.13637733459472656 seconds to complete, which may be a performance bottleneck.


== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/8 CPUs, 0/0 GPUs
Memory usage on this node: 41.5/67.5 GB
Result logdir: logs/GAIAPredictorsContinuousV8_1-01-01_to_2007-12-31
Number of trials: 6 ({'RUNNING': 1, 'PENDING': 5})
PENDING trials:
 - PPO_GAIAPredictorsContinuousV8_restoreID=5767707966177719730_runID=VQ6ZSlxh_1_clip_param=0.2,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000:	PENDING
 - PPO_GAIAPredictorsContinuousV8_restoreID=-3901639819934833792_runID=VQ6ZSlxh_2_clip_param=0.3,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000:	PENDING
 - PPO_GAIAPredictorsContinuousV8_restoreID=8837309464980678580_runID=VQ6ZSlxh_3_clip_param=0.4,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000:	PENDING
 - PPO_GAIAPredictorsConti

(pid=51014) 2019-07-18 16:43:47,659	INFO dynamic_tf_policy.py:313 -- Initializing loss function with dummy input:
(pid=51014) 
(pid=51014) { 'action_prob': <tf.Tensor 'default_policy/action_prob:0' shape=(?,) dtype=float32>,
(pid=51014)   'actions': <tf.Tensor 'default_policy/actions:0' shape=(?, 2) dtype=float32>,
(pid=51014)   'advantages': <tf.Tensor 'default_policy/advantages:0' shape=(?,) dtype=float32>,
(pid=51014)   'behaviour_logits': <tf.Tensor 'default_policy/behaviour_logits:0' shape=(?, 2) dtype=float32>,
(pid=51014)   'dones': <tf.Tensor 'default_policy/dones:0' shape=(?,) dtype=bool>,
(pid=51014)   'new_obs': <tf.Tensor 'default_policy/new_obs:0' shape=(?, 5) dtype=float32>,
(pid=51014)   'obs': <tf.Tensor 'default_policy/observation:0' shape=(?, 5) dtype=float32>,
(pid=51014)   'prev_actions': <tf.Tensor 'default_policy/action:0' shape=(?, 2) dtype=float32>,
(pid=51014)   'prev_rewards': <tf.Tensor 'default_policy/prev_reward:0' shape=(?,) dtype=float32>,
(pid=51014)   '

...

(pid=100648) 2019-07-18 19:14:18,811	WARNING ppo.py:129 -- The magnitude of your environment rewards are more than infx the scale of `vf_clip_param`. This means that it will take more than inf iterations for your value function to converge. If this is not intended, consider increasing `vf_clip_param`.


2019-07-18 19:14:22,785	INFO ray_trial_executor.py:187 -- Destroying actor for trial PPO_GAIAPredictorsContinuousV8_restoreID=7122607550531400491_runID=VQ6ZSlxh_4_clip_param=0.5,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000. If your trainable is slow to initialize, consider setting reuse_actors=True to reduce actor creation overheads.
2019-07-18 19:14:22,788	WARNING util.py:64 -- The `process_trial` operation took 0.15548348426818848 seconds to complete, which may be a performance bottleneck.
2019-07-18 19:14:23,278	WARNING util.py:64 -- The `experiment_checkpoint` operation took 0.48774099349975586 seconds to complete, which may be a performance bottleneck.


(pid=113222) 2019-07-18 19:14:23,242	WARNING ppo.py:129 -- The magnitude of your environment rewards are more than infx the scale of `vf_clip_param`. This means that it will take more than inf iterations for your value function to converge. If this is not intended, consider increasing `vf_clip_param`.
== Status ==
Using FIFO scheduling algorithm.
Resources requested: 3/8 CPUs, 0/0 GPUs
Memory usage on this node: 44.6/67.5 GB
Result logdir: logs/GAIAPredictorsContinuousV8_1-01-01_to_2008-12-31
Number of trials: 6 ({'TERMINATED': 5, 'RUNNING': 1})
RUNNING trials:
 - PPO_GAIAPredictorsContinuousV8_restoreID=1308361796297373496_runID=VQ6ZSlxh_5_clip_param=0.6,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000:	RUNNING, [3 CPUs, 0 GPUs], [pid=113222], 1212 s, 74 iter, 296000 ts, 0.00424 rew
TERMINATED trials:
 - PPO_GAIAPredictorsContinuousV8_restoreID=-5439106634883206763_runID=VQ6ZSlxh_0_clip_param=0.1,entrop

2019-07-18 19:14:26,652	INFO ray_trial_executor.py:187 -- Destroying actor for trial PPO_GAIAPredictorsContinuousV8_restoreID=1308361796297373496_runID=VQ6ZSlxh_5_clip_param=0.6,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000. If your trainable is slow to initialize, consider setting reuse_actors=True to reduce actor creation overheads.
2019-07-18 19:14:26,655	WARNING util.py:64 -- The `process_trial` operation took 0.11952328681945801 seconds to complete, which may be a performance bottleneck.
2019-07-18 19:14:26,861	WARNING util.py:64 -- The `experiment_checkpoint` operation took 0.19758391380310059 seconds to complete, which may be a performance bottleneck.


== Status ==
Using FIFO scheduling algorithm.
Resources requested: 0/8 CPUs, 0/0 GPUs
Memory usage on this node: 43.8/67.5 GB
Result logdir: logs/GAIAPredictorsContinuousV8_1-01-01_to_2008-12-31
Number of trials: 6 ({'TERMINATED': 6})
TERMINATED trials:
 - PPO_GAIAPredictorsContinuousV8_restoreID=-5439106634883206763_runID=VQ6ZSlxh_0_clip_param=0.1,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000:	TERMINATED, [3 CPUs, 0 GPUs], [pid=76728], 1186 s, 75 iter, 300000 ts, 0.00534 rew
 - PPO_GAIAPredictorsContinuousV8_restoreID=5767707966177719730_runID=VQ6ZSlxh_1_clip_param=0.2,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000:	TERMINATED, [3 CPUs, 0 GPUs], [pid=76716], 1175 s, 75 iter, 300000 ts, 0.00796 rew
 - PPO_GAIAPredictorsContinuousV8_restoreID=-3901639819934833792_runID=VQ6ZSlxh_2_clip_param=0.3,entropy_coeff=1e-05,cost

Note that trials are associated with a `RestoreID`. This `ID` is all you need to restore an agent. Here we are using a grid search of two values for `cost_of_commissions` on two partitions, so we have a total of 4 experiments.

In [23]:
trials

[PPO_GAIAPredictorsContinuousV8_restoreID=2518378458784788772_runID=1k09BnXl_0_clip_param=0.6,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000,
 PPO_GAIAPredictorsContinuousV8_restoreID=-8787645495220943684_runID=1k09BnXl_1_clip_param=0.7,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000,
 PPO_GAIAPredictorsContinuousV8_restoreID=-6239325116953107123_runID=1k09BnXl_2_clip_param=0.8,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000,
 PPO_GAIAPredictorsContinuousV8_restoreID=-8406265528539338280_runID=1k09BnXl_3_clip_param=0.9,entropy_coeff=1e-05,cost_of_commissions=5e-05,gamma=1e-05,kl_coeff=0.2,kl_target=0.01,lr=1e-05,num_sgd_iter=8,train_batch_size=4000,
 PPO_GAIAPredictorsContinuousV8_restoreID=2518378458784788772_runID=1k09BnXl_0_clip_param

You can monitor agents' training in tensorboard.
![title](tensorboard.png)

# WalkForwardResults

`WalkForwardResults` is the 'controller' of all your walk forward results across all environment you have solved using `WalkForwardRunner`. If you print the class instance, you will see the list of all environments that you've solved.

In [15]:
results = WalkForwardResults(path=os.path.join(os.getcwd(), 'logs'))
results

WalkForwardResults(['GAIAPredictorsContinuousV8'])

Let's select the results associated with a particular environment.

In [16]:
env_results = results['GAIAPredictorsContinuousV8']
env_results

EnvResults(GAIAPredictorsContinuousV8)

To assess an agent on an env you need an agent and an env. That's all we are trying to do here. Steps:

1. `EnvResults.make_env`: this method allows you to restore an environment and gives you the possibility to pass a new `env_config` (e.g. different transaction costs). Note that this flexibility allows you to train on given `env_config` (e.g. unrealistically high transaction costs) and assess using different configurations (e.g. realistic transaction costs).
2. `EnvResults.make_policy`: this method allows you to implement an `AbstractPolicy` which is needed to sample episodes from `TradingEnv` and thus render the results. Arguments of this method allows you to specify stuff like:
    1. Which agent's checkpoint to use (last $n$). If blank the last checkpoint will be used (i.e. last training iteration). If $n>1$, then a list of actions will be returned (one for each agent).
    2. Whether or not to create an esample from the previously trained agents.
3. `episode.TradingEnv.sample_episode(policy)`: returns an instance of `Episode`. Charts and tables can be produced using `Episode.render`. `episode` stores all information you need to assess your agent.

In [17]:
# Step 1.
env = env_results.make_env(
    env_config={
        'cost_of_commissions': 0.00005,
        'cost_of_spread': 0.0001,
        'folds': {
            'training-set': [datetime.min, datetime(2008, 3, 18)],
            'test-set': [datetime(2008, 3, 19), datetime.max],
        }
    },
)

Note that these are the same `RestoreID`s that we so in the previous section.

In [18]:
# I would like to get in all the ids that have the clip parameters..

In [19]:
env_results.restore_ids

{7598463039896949665: [AgentResults(GAIAPredictorsContinuousV8_1-01-01_to_2007-12-31/PPO_GAIAPredictorsContinuousV8_restoreID=7598463039896949665_runID=xZhYdK7w_3_clip_param=0.9,entropy_coeff=1e-05,cost_of_commissio_2019-07-18_13-38-13kwfwp3oo),
  AgentResults(GAIAPredictorsContinuousV8_1-01-01_to_2008-12-31/PPO_GAIAPredictorsContinuousV8_restoreID=7598463039896949665_runID=xZhYdK7w_3_clip_param=0.9,entropy_coeff=1e-05,cost_of_commissio_2019-07-18_14-57-20h4p6ma0t)],
 8837309464980678580: [AgentResults(GAIAPredictorsContinuousV8_1-01-01_to_2007-12-31/PPO_GAIAPredictorsContinuousV8_restoreID=8837309464980678580_runID=VQ6ZSlxh_3_clip_param=0.4,entropy_coeff=1e-05,cost_of_commissio_2019-07-18_17-08-438n1jeljd),
  AgentResults(GAIAPredictorsContinuousV8_1-01-01_to_2008-12-31/PPO_GAIAPredictorsContinuousV8_restoreID=8837309464980678580_runID=VQ6ZSlxh_3_clip_param=0.4,entropy_coeff=1e-05,cost_of_commissio_2019-07-18_18-23-120ssc446k)],
 7122607550531400491: [AgentResults(GAIAPredictorsContin

In [185]:
# We select a whatever id here (the first). 
# If you want to restore a particular run from tensorboard, just check RestoreID and specify it here.
#  Have to check the clip parameters from the fiels to actually see this
restore_id = list(env_results.restore_ids)
restore_id

[7598463039896949665,
 8837309464980678580,
 7122607550531400491,
 1308361796297373496,
 5767707966177719730,
 -5439106634883206763,
 -4098264995593170541,
 -3901639819934833792,
 7573595310785109233,
 7275111392035880491,
 2757953976683739850,
 4505214956857783623]

In order: <br>
0.9 <br>
0.4<br>
0.5<br>
0.6<br>
0.2<br>
0.1<br>
1.1<br>
0.3<br>
0.6<br>
1.0<br>
0.8<br>
0.7<br>

In [186]:
restore_id = restore_id[11]

In [187]:
# Step 2.
policy = env_results.make_policy(
    env=env,
    restore_id=restore_id,
    checkpoint_nr=5,  # use None (or don't specify) to use last checkpoint available
)
policy

In the previous chapters we have used `WalkForwardRunner` to run a walk forward optimization re-training every year. In other circumstances, re-training might follow more complex patterns. For example re-training might occur on an irregular basis, e.g. whenever there is a structural break in the markets. So it might be useful to visualize the "age" of the model used in a given day. The older the model, the higher the risk that there has been a change in the dynamics of the system and so the model might be out-dated.

In [188]:
history = policy.history()
history

AgeInDays              FoldEnd            RestoreID
2008-01-01         1  2007-12-31 00:00:00  4505214956857783623
2008-01-02         2  2007-12-31 00:00:00  4505214956857783623
2008-01-03         3  2007-12-31 00:00:00  4505214956857783623
2008-01-04         4  2007-12-31 00:00:00  4505214956857783623
2008-01-07         7  2007-12-31 00:00:00  4505214956857783623
2008-01-08         8  2007-12-31 00:00:00  4505214956857783623
2008-01-09         9  2007-12-31 00:00:00  4505214956857783623
2008-01-10        10  2007-12-31 00:00:00  4505214956857783623
2008-01-11        11  2007-12-31 00:00:00  4505214956857783623
2008-01-14        14  2007-12-31 00:00:00  4505214956857783623
2008-01-15        15  2007-12-31 00:00:00  4505214956857783623
2008-01-16        16  2007-12-31 00:00:00  4505214956857783623
2008-01-17        17  2007-12-31 00:00:00  4505214956857783623
2008-01-18        18  2007-12-31 00:00:00  4505214956857783623
2008-01-21        21  2007-12-31 00:00:00  4505214956857783623
2008-01-22        22  2007-12-31 00:00:00  4505214956857783623
2008-01-23        23  2007-12-31 00:00:00  4505214956857783623
2008-01-24        24  2007-12-31 00:00:00  4505214956857783623
2008-01-25        25  2007-12-31 00:00:00  4505214956857783623
2008-01-28        28  2007-12-31 00:00:00  4505214956857783623
2008-01-29        29  2007-12-31 00:00:00  4505214956857783623
2008-01-30        30  2007-12-31 00:00:00  4505214956857783623
2008-01-31        31  2007-12-31 00:00:00  4505214956857783623
2008-02-01        32  2007-12-31 00:00:00  4505214956857783623
2008-02-04        35  2007-12-31 00:00:00  4505214956857783623
2008-02-05        36  2007-12-31 00:00:00  4505214956857783623
2008-02-06        37  2007-12-31 00:00:00  4505214956857783623
2008-02-07        38  2007-12-31 00:00:00  4505214956857783623
2008-02-08        39  2007-12-31 00:00:00  4505214956857783623
2008-02-11        42  2007-12-31 00:00:00  4505214956857783623
...              ...                  ...                  ...
2010-11-22       691  2008-12-31 00:00:00  4505214956857783623
2010-11-23       692  2008-12-31 00:00:00  4505214956857783623
2010-11-24       693  2008-12-31 00:00:00  4505214956857783623
2010-11-25       694  2008-12-31 00:00:00  4505214956857783623
2010-11-26       695  2008-12-31 00:00:00  4505214956857783623
2010-11-29       698  2008-12-31 00:00:00  4505214956857783623
2010-11-30       699  2008-12-31 00:00:00  4505214956857783623
2010-12-01       700  2008-12-31 00:00:00  4505214956857783623
2010-12-02       701  2008-12-31 00:00:00  4505214956857783623
2010-12-03       702  2008-12-31 00:00:00  4505214956857783623
2010-12-06       705  2008-12-31 00:00:00  4505214956857783623
2010-12-07       706  2008-12-31 00:00:00  4505214956857783623
2010-12-08       707  2008-12-31 00:00:00  4505214956857783623
2010-12-09       708  2008-12-31 00:00:00  4505214956857783623
2010-12-10       709  2008-12-31 00:00:00  4505214956857783623
2010-12-13       712  2008-12-31 00:00:00  4505214956857783623
2010-12-14       713  2008-12-31 00:00:00  4505214956857783623
2010-12-15       714  2008-12-31 00:00:00  4505214956857783623
2010-12-16       715  2008-12-31 00:00:00  4505214956857783623
2010-12-17       716  2008-12-31 00:00:00  4505214956857783623
2010-12-20       719  2008-12-31 00:00:00  4505214956857783623
2010-12-21       720  2008-12-31 00:00:00  4505214956857783623
2010-12-22       721  2008-12-31 00:00:00  4505214956857783623
2010-12-23       722  2008-12-31 00:00:00  4505214956857783623
2010-12-24       723  2008-12-31 00:00:00  4505214956857783623
2010-12-27       726  2008-12-31 00:00:00  4505214956857783623
2010-12-28       727  2008-12-31 00:00:00  4505214956857783623
2010-12-29       728  2008-12-31 00:00:00  4505214956857783623
2010-12-30       729  2008-12-31 00:00:00  4505214956857783623
2010-12-31       730  2008-12-31 00:00:00  4505214956857783623

[784 rows x 3 columns]

In [189]:
history['AgeInDays'].iplot(
    title='Age in days of the most recent model that could be used in the date indicated in the x-axis<br>Whenever the count drops to zero, there has been a re-training of the model',
    yTitle='Nr of days',
    fill=True,
)

In [190]:
# Step 3.
episode = env.sample_episode(fold='test-set', policy=policy, verbose=False)

2019-07-24 09:42:25,449	WARNING ppo.py:151 -- FYI: By default, the value function will not share layers with the policy model ('vf_share_layers': False).
2019-07-24 09:42:26,870	INFO rollout_worker.py:301 -- Creating policy evaluation worker 0 on CPU (please ignore any CUDA init errors)
2019-07-24 09:42:28,884	INFO rollout_worker.py:719 -- Built policy map: {'default_policy': <ray.rllib.policy.tf_policy_template.PPOTFPolicy object at 0x7fb7aee20a90>}
2019-07-24 09:42:28,885	INFO rollout_worker.py:720 -- Built preprocessor map: {'default_policy': <ray.rllib.models.preprocessors.NoPreprocessor object at 0x7fb7aee20668>}
2019-07-24 09:42:28,886	INFO rollout_worker.py:333 -- Built filter map: {'default_policy': <ray.rllib.utils.filter.NoFilter object at 0x7fb7aee20438>}
2019-07-24 09:42:28,937	INFO multi_gpu_optimizer.py:79 -- LocalMultiGPUOptimizer devices ['/cpu:0']
2019-07-24 09:42:34,535	WARNING ppo.py:151 -- FYI: By default, the value function will not share layers with the policy mod

Render results over the combined test-folds
`episode.renderer` is probably the single most useful attribute of `Episode` to visualize results, but you are invited to explore other attributes such as `episode.states` or `episode.actions`.

In [191]:
episode.renderer.cumulative_performance.to_plotly()
episode.renderer.target_weights.to_plotly()
episode.renderer.annual_returns.to_plotly()
episode.renderer.tearsheet()

Strategy  \
Context              From                                       2008-03-19   
                     To                                         2018-08-28   
                     Years                                         10.4493   
                     Observations                                     2725   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                             0.00681294   
Return               CAGR                                         0.100896   
                     CAGR over cash                              0.0940827   
                     Overall return                                1.73035   
Risk                 Volatility                                   0.075678   
                     Downside volatility                         0.0546096   
                     Upside volatility                           0.0531877   
                     Max drawdown                               -0.0907077   
                     Martin risk                                 0.0199585   
                     VaR 5%                                    -0.00719734   
                     VaR 2%                                     -0.0105443   
                     Expected shortfall 5%                      -0.0108076   
                     Expected shortfall 2%                      -0.0140263   
Risk-adjusted return Sharpe ratio                                   1.2432   
                     Sortino ratio                                 1.72282   
                     Calmar ratio                                  1.03721   
                     Martin ratio                                  4.71392   
Outperformance       Benchmark name                  Index(Aric-Benchmark)   
                     CAGR over benchmark                        -0.0576899   
                     Information ratio                           -0.936217   
                     CAPM Alpha                                 0.00459604   
                     CAPM Beta                                     0.60259   
Weights              Cash(USD)                                           0   
                     ETF(Russell 1000, SMART, USD)                0.408404   
                     ETF(7-10Y T-Bills, SMART, USD)               0.591596   
                     Leverage mean                                       1   
                     Turnover daily                              0.0301495   
                     Turnover annual                               7.59767   

                                                     Index(Aric-Benchmark)  \
Context              From                                       2008-03-19   
                     To                                         2018-08-28   
                     Years                                         10.4493   
                     Observations                                     2725   
                     Risk-free asset                 Index(USD 1M Deposit)   
                     Risk-free CAGR                             0.00681294   
Return               CAGR                                         0.158586   
                     CAGR over cash                               0.151773   
                     Overall return                                3.65592   
Risk                 Volatility                                  0.0970738   
                     Downside volatility                          0.069906   
                     Upside volatility                           0.0705399   
                     Max drawdown                               -0.0865477   
                     Martin risk                                 0.0189993   
                     VaR 5%                                    -0.00895352   
                     VaR 2%                                     -0.0134313   
                     Expected shortfall 5%                      -0.0137858   
         

## Use case: interactive charts with widgets to visualize the agent during training
How do the historical test-set weights change as we train? By default, one call to `agent.train` runs the agent for 4000 timesteps. We previously set `checkpoint_freq=1`, so we will be able to restore agents every 4000 timesteps.

In [192]:
import numpy as np

In [193]:
# This might take long as it requires to restore #agents \times #nr_checkpoints
z = list(np.arange(1,76,5))
# z.append(75)

nr2episode = env_results.get_nr2episode(
    restore_id=restore_id,
    checkpoint_nrs= z,
    #checkpoint_nrs=[1, 2, 3, 4, 5, 6, 7],
    fold='test-set',
    env_config={
        'folds': {
            'training-set': [datetime.min, datetime(2008, 3, 18)],
            'test-set': [datetime(2008, 3, 19), datetime.max],
        }
    }
)
nr2episode

{1: <trading_gym.env.Episode at 0x7fb7a4ddd390>,
 6: <trading_gym.env.Episode at 0x7fb7a5299748>,
 11: <trading_gym.env.Episode at 0x7fb7a4a5a5c0>,
 16: <trading_gym.env.Episode at 0x7fb7b2641a58>,
 21: <trading_gym.env.Episode at 0x7fb7a4a5aa90>,
 26: <trading_gym.env.Episode at 0x7fb7a4ddd860>,
 31: <trading_gym.env.Episode at 0x7fb7a3dec278>,
 36: <trading_gym.env.Episode at 0x7fb7a40dbf98>,
 41: <trading_gym.env.Episode at 0x7fb7a3438a20>,
 46: <trading_gym.env.Episode at 0x7fb7a3151588>,
 51: <trading_gym.env.Episode at 0x7fb7a2e5dd68>,
 56: <trading_gym.env.Episode at 0x7fb7a2afac50>,
 61: <trading_gym.env.Episode at 0x7fb7a28137b8>,
 66: <trading_gym.env.Episode at 0x7fb7a2525f60>,
 71: <trading_gym.env.Episode at 0x7fb7a21bde48>}

In [194]:
nr2episode.plot_weights()

interactive(children=(IntSlider(value=36, description='nr', max=108, min=-36), Output()), _dom_classes=('widge…

FigureWidget({
    'data': [{'name': 'Cash(USD)',
              'type': 'scatter',
              'uid': 'cc48b…

In [195]:
nr2episode.plot_levels()

interactive(children=(IntSlider(value=36, description='nr', max=108, min=-36), Output()), _dom_classes=('widge…

FigureWidget({
    'data': [{'name': 'Strategy',
              'type': 'scatter',
              'uid': '908933…

In [196]:
nr2episode.plot_metrics_as_we_train()